In [1]:
LIST_OF_SUBREDDITS_TEXTFILE = "./final_list_of_subreddits.csv"
SUBREDDIT_METADATA_FILE = "./subreddit_metadata.json"
CLIENT_ID = "tr8N3_dbpOW4R_v0XRfE-A"
CLIENT_SECRET = "juZTa0fGt0L1TauVrVgAnybz-M6RSQ"
APP_NAME = "modCrawlerBOT"
USER_NAME = "ModCrawlBOT"
USER_PASSWORD = "NetSci4Web"
USER_AGENT = "ThisAgent"
OAUTH_URL_PREFIX = "https://oauth.reddit.com"


import requests
import requests.auth
import time 
import json 
import pandas as pd
import csv
from joblib import Parallel, delayed 

def get_reddit_oauth2_token():
    client_auth = requests.auth.HTTPBasicAuth(CLIENT_ID,CLIENT_SECRET)
    post_data = {"grant_type":"password","username":USER_NAME,"password":USER_PASSWORD}
    headers = {"User-Agent":"Quasimodo v0.1"} 
    response = requests.post("https://www.reddit.com/api/v1/access_token", auth=client_auth, data=post_data,
                         headers=headers)
    return response

def get_authenticated_reddit_request(url): 
    return requests.get(url,headers=HEADERS)

print("Authenticating...")
ACCESS_TOKEN = get_reddit_oauth2_token().json()['access_token']
HEADERS = {"Authorization": "bearer "+ACCESS_TOKEN, "User-Agent": USER_AGENT}


print("Authenticated. Received ACCESS_TOKEN", ACCESS_TOKEN)

Authenticating...
Authenticated. Received ACCESS_TOKEN 2370748322945-C_YfVxhrdDu24UzJEGoe3tB7vkeuHg


In [12]:
rq = get_authenticated_reddit_request(OAUTH_URL_PREFIX+ "/r/0hio/about/")
rqjs = rq.json()

rq = get_authenticated_reddit_request(OAUTH_URL_PREFIX+ "/r/0hio/about/moderators/")
rqjs2 = rq.json()
rqjs2
rqjs['data']['mods'] = rqjs2['data']
#with open("./Subreddits/AskReddit.csv", "w") as f:
#    json.dump(rqjs['data'],f)

In [13]:
rqjs2

{'kind': 'UserList', 'data': {'children': []}}

In [9]:
path_list = []
with open("subs.csv",'r') as f:
    path_list = list(csv.reader(f))
j = 0
for i in path_list:
    path_list[j] = i[0]
    j+=1

In [10]:
def get_subreddit_info(subname):
    path = "./Subreddits/"+subname+".csv"
    try:
        rq = get_authenticated_reddit_request(OAUTH_URL_PREFIX+ "/r/"+subname+"/about/")
        if rq.status_code != 200:
            return 0
        with open(path,'w') as f:
            rqjs = rq.json()
            mods = get_authenticated_reddit_request(OAUTH_URL_PREFIX+ "/r/"+subname+"/about/moderators/")
            modsjs = mods.json()
            #rqjs["data"]["mods"] = modsjs["data"]
            json.dump([rqjs['data'],modsjs['data']],f)
            #json.dump(modsjs['data'],f)
        return 1
    except:
        return 0

In [11]:
#Warning, the below could be RAM-hungry. It may also be CPU-hungry.
subreddits_lstlst = Parallel(n_jobs=100, prefer = "threads", pre_dispatch=400,verbose=20)(delayed(get_subreddit_info)(i) for i in path_list)

[Parallel(n_jobs=100)]: Using backend ThreadingBackend with 100 concurrent workers.
[Parallel(n_jobs=100)]: Done   1 tasks      | elapsed:    0.7s
[Parallel(n_jobs=100)]: Done   2 tasks      | elapsed:    0.7s
[Parallel(n_jobs=100)]: Done   3 tasks      | elapsed:    0.7s
[Parallel(n_jobs=100)]: Done   4 tasks      | elapsed:    0.7s
[Parallel(n_jobs=100)]: Done   5 tasks      | elapsed:    0.9s
[Parallel(n_jobs=100)]: Done   6 tasks      | elapsed:    0.9s
[Parallel(n_jobs=100)]: Done   7 tasks      | elapsed:    0.9s
[Parallel(n_jobs=100)]: Done   8 tasks      | elapsed:    0.9s
[Parallel(n_jobs=100)]: Done   9 tasks      | elapsed:    1.2s
[Parallel(n_jobs=100)]: Done  10 tasks      | elapsed:    1.2s
[Parallel(n_jobs=100)]: Done  11 tasks      | elapsed:    1.2s
[Parallel(n_jobs=100)]: Done  12 tasks      | elapsed:    1.3s
[Parallel(n_jobs=100)]: Done  13 tasks      | elapsed:    1.3s
[Parallel(n_jobs=100)]: Done  14 tasks      | elapsed:    1.3s
[Parallel(n_jobs=100)]: Done  15 t

In [11]:
import multiprocessing

def get_all_data():
    pool = multiprocessing.Pool(processes=6)
    res = pool.map(get_subreddit_info,path_list)

In [ ]:
get_all_data()